In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
# Convolutional neural network (two convolutional layers)
class Transformer(nn.Module):
    def __init__(self, num_classes=4):
        super(Transformer, self).__init__()
           
        self.encoder_layer = nn.TransformerEncoderLayer(d_model=64, nhead=8)
        self.transformer_encoder = nn.TransformerEncoder(self.encoder_layer, num_layers=6)
        self.pool = nn.MaxPool1d(64)
        
        self.d1 = nn.Dropout(p=0.25)
        #self.d2 = nn.Dropout(p=0.25)
        
        self.fc1 = nn.Linear(64, num_classes)
        #self.fc2 = nn.Linear(num_classes, 1)
        
    def forward(self, x):      
        
        x = self.transformer_encoder(x)
        x = self.pool(x)
        x = x.reshape(-1,64)
        x = self.d1(x)
        x = self.fc1(x)
        #x = F.relu(x)
        #x = self.d2(x)
        #x = self.fc2(x)
        #x = F.sigmoid(x)
        

        return x

In [3]:
rnn = Transformer(4)
input = torch.randn(10, 64, 64)
output= rnn(input)
print(output.shape)

torch.Size([10, 4])


In [4]:
writer = SummaryWriter()

In [5]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [6]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [8]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [9]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [10]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [11]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [12]:
model = Transformer(num_classes).to(device)

In [15]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [16]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        #outputs = torch.squeeze(outputs)
        #Y = Y.float()
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 35.9375%, Training Loss: 2.2890%
Epoch [1/300], Step [2/225], Training Accuracy: 28.9062%, Training Loss: 2.4214%
Epoch [1/300], Step [3/225], Training Accuracy: 26.0417%, Training Loss: 2.3276%
Epoch [1/300], Step [4/225], Training Accuracy: 25.7812%, Training Loss: 2.1615%
Epoch [1/300], Step [5/225], Training Accuracy: 25.6250%, Training Loss: 2.0823%
Epoch [1/300], Step [6/225], Training Accuracy: 23.6979%, Training Loss: 2.0153%
Epoch [1/300], Step [7/225], Training Accuracy: 23.6607%, Training Loss: 1.9493%
Epoch [1/300], Step [8/225], Training Accuracy: 24.4141%, Training Loss: 1.8996%
Epoch [1/300], Step [9/225], Training Accuracy: 25.0000%, Training Loss: 1.8574%
Epoch [1/300], Step [10/225], Training Accuracy: 24.8438%, Training Loss: 1.8251%
Epoch [1/300], Step [11/225], Training Accuracy: 25.0000%, Training Loss: 1.7947%
Epoch [1/300], Step [12/225], Training Accuracy: 25.6510%, Training Loss: 1.7619%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [108/225], Training Accuracy: 25.1302%, Training Loss: 1.4583%
Epoch [1/300], Step [109/225], Training Accuracy: 25.0860%, Training Loss: 1.4578%
Epoch [1/300], Step [110/225], Training Accuracy: 25.1562%, Training Loss: 1.4570%
Epoch [1/300], Step [111/225], Training Accuracy: 25.1548%, Training Loss: 1.4564%
Epoch [1/300], Step [112/225], Training Accuracy: 25.1953%, Training Loss: 1.4554%
Epoch [1/300], Step [113/225], Training Accuracy: 25.1659%, Training Loss: 1.4554%
Epoch [1/300], Step [114/225], Training Accuracy: 25.2330%, Training Loss: 1.4546%
Epoch [1/300], Step [115/225], Training Accuracy: 25.1495%, Training Loss: 1.4546%
Epoch [1/300], Step [116/225], Training Accuracy: 25.0808%, Training Loss: 1.4544%
Epoch [1/300], Step [117/225], Training Accuracy: 25.0534%, Training Loss: 1.4541%
Epoch [1/300], Step [118/225], Training Accuracy: 25.0265%, Training Loss: 1.4539%
Epoch [1/300], Step [119/225], Training Accuracy: 25.0525%, Training Loss: 1.4535%
Epoc

Epoch [1/300], Step [210/225], Training Accuracy: 25.5357%, Training Loss: 1.4283%
Epoch [1/300], Step [211/225], Training Accuracy: 25.5702%, Training Loss: 1.4279%
Epoch [1/300], Step [212/225], Training Accuracy: 25.5454%, Training Loss: 1.4279%
Epoch [1/300], Step [213/225], Training Accuracy: 25.5502%, Training Loss: 1.4278%
Epoch [1/300], Step [214/225], Training Accuracy: 25.5549%, Training Loss: 1.4279%
Epoch [1/300], Step [215/225], Training Accuracy: 25.5669%, Training Loss: 1.4277%
Epoch [1/300], Step [216/225], Training Accuracy: 25.5353%, Training Loss: 1.4277%
Epoch [1/300], Step [217/225], Training Accuracy: 25.5616%, Training Loss: 1.4276%
Epoch [1/300], Step [218/225], Training Accuracy: 25.5304%, Training Loss: 1.4275%
Epoch [1/300], Step [219/225], Training Accuracy: 25.5208%, Training Loss: 1.4273%
Epoch [1/300], Step [220/225], Training Accuracy: 25.5327%, Training Loss: 1.4273%
Epoch [1/300], Step [221/225], Training Accuracy: 25.5303%, Training Loss: 1.4272%
Epoc

Epoch [2/300], Step [91/225], Training Accuracy: 25.7040%, Training Loss: 1.3989%
Epoch [2/300], Step [92/225], Training Accuracy: 25.7133%, Training Loss: 1.3989%
Epoch [2/300], Step [93/225], Training Accuracy: 25.8401%, Training Loss: 1.3984%
Epoch [2/300], Step [94/225], Training Accuracy: 25.7646%, Training Loss: 1.3988%
Epoch [2/300], Step [95/225], Training Accuracy: 25.7237%, Training Loss: 1.3989%
Epoch [2/300], Step [96/225], Training Accuracy: 25.6836%, Training Loss: 1.3988%
Epoch [2/300], Step [97/225], Training Accuracy: 25.7732%, Training Loss: 1.3984%
Epoch [2/300], Step [98/225], Training Accuracy: 25.8291%, Training Loss: 1.3982%
Epoch [2/300], Step [99/225], Training Accuracy: 25.8049%, Training Loss: 1.3980%
Epoch [2/300], Step [100/225], Training Accuracy: 25.7031%, Training Loss: 1.3982%
Epoch [2/300], Step [101/225], Training Accuracy: 25.7271%, Training Loss: 1.3980%
Epoch [2/300], Step [102/225], Training Accuracy: 25.7659%, Training Loss: 1.3980%
Epoch [2/300]

Epoch [2/300], Step [194/225], Training Accuracy: 25.9665%, Training Loss: 1.3967%
Epoch [2/300], Step [195/225], Training Accuracy: 25.9455%, Training Loss: 1.3967%
Epoch [2/300], Step [196/225], Training Accuracy: 25.9088%, Training Loss: 1.3968%
Epoch [2/300], Step [197/225], Training Accuracy: 25.9201%, Training Loss: 1.3968%
Epoch [2/300], Step [198/225], Training Accuracy: 25.9075%, Training Loss: 1.3969%
Epoch [2/300], Step [199/225], Training Accuracy: 25.8872%, Training Loss: 1.3969%
Epoch [2/300], Step [200/225], Training Accuracy: 25.8828%, Training Loss: 1.3969%
Epoch [2/300], Step [201/225], Training Accuracy: 25.8473%, Training Loss: 1.3970%
Epoch [2/300], Step [202/225], Training Accuracy: 25.8973%, Training Loss: 1.3968%
Epoch [2/300], Step [203/225], Training Accuracy: 25.9006%, Training Loss: 1.3968%
Epoch [2/300], Step [204/225], Training Accuracy: 25.8885%, Training Loss: 1.3968%
Epoch [2/300], Step [205/225], Training Accuracy: 25.8765%, Training Loss: 1.3968%
Epoc

...

Epoch [298/300], Step [176/225], Training Accuracy: 93.6523%, Training Loss: 0.2005%
Epoch [298/300], Step [177/225], Training Accuracy: 93.6352%, Training Loss: 0.2006%
Epoch [298/300], Step [178/225], Training Accuracy: 93.6534%, Training Loss: 0.2005%
Epoch [298/300], Step [179/225], Training Accuracy: 93.6802%, Training Loss: 0.2004%
Epoch [298/300], Step [180/225], Training Accuracy: 93.6545%, Training Loss: 0.2006%
Epoch [298/300], Step [181/225], Training Accuracy: 93.6637%, Training Loss: 0.2009%
Epoch [298/300], Step [182/225], Training Accuracy: 93.6727%, Training Loss: 0.2005%
Epoch [298/300], Step [183/225], Training Accuracy: 93.6646%, Training Loss: 0.2009%
Epoch [298/300], Step [184/225], Training Accuracy: 93.6651%, Training Loss: 0.2008%
Epoch [298/300], Step [185/225], Training Accuracy: 93.6824%, Training Loss: 0.2007%
Epoch [298/300], Step [186/225], Training Accuracy: 93.6996%, Training Loss: 0.2003%
Epoch [298/300], Step [187/225], Training Accuracy: 93.6999%, Tra

Epoch [299/300], Step [52/225], Training Accuracy: 93.6899%, Training Loss: 0.2022%
Epoch [299/300], Step [53/225], Training Accuracy: 93.6321%, Training Loss: 0.2045%
Epoch [299/300], Step [54/225], Training Accuracy: 93.5764%, Training Loss: 0.2050%
Epoch [299/300], Step [55/225], Training Accuracy: 93.5795%, Training Loss: 0.2046%
Epoch [299/300], Step [56/225], Training Accuracy: 93.5826%, Training Loss: 0.2049%
Epoch [299/300], Step [57/225], Training Accuracy: 93.5033%, Training Loss: 0.2054%
Epoch [299/300], Step [58/225], Training Accuracy: 93.4267%, Training Loss: 0.2070%
Epoch [299/300], Step [59/225], Training Accuracy: 93.4852%, Training Loss: 0.2057%
Epoch [299/300], Step [60/225], Training Accuracy: 93.5417%, Training Loss: 0.2050%
Epoch [299/300], Step [61/225], Training Accuracy: 93.5451%, Training Loss: 0.2049%
Epoch [299/300], Step [62/225], Training Accuracy: 93.5232%, Training Loss: 0.2050%
Epoch [299/300], Step [63/225], Training Accuracy: 93.5020%, Training Loss: 

Epoch [299/300], Step [152/225], Training Accuracy: 93.7397%, Training Loss: 0.1994%
Epoch [299/300], Step [153/225], Training Accuracy: 93.7500%, Training Loss: 0.1993%
Epoch [299/300], Step [154/225], Training Accuracy: 93.7399%, Training Loss: 0.1998%
Epoch [299/300], Step [155/225], Training Accuracy: 93.7298%, Training Loss: 0.2001%
Epoch [299/300], Step [156/225], Training Accuracy: 93.7700%, Training Loss: 0.1995%
Epoch [299/300], Step [157/225], Training Accuracy: 93.7500%, Training Loss: 0.1996%
Epoch [299/300], Step [158/225], Training Accuracy: 93.7203%, Training Loss: 0.2000%
Epoch [299/300], Step [159/225], Training Accuracy: 93.7107%, Training Loss: 0.2001%
Epoch [299/300], Step [160/225], Training Accuracy: 93.7109%, Training Loss: 0.1998%
Epoch [299/300], Step [161/225], Training Accuracy: 93.7112%, Training Loss: 0.2001%
Epoch [299/300], Step [162/225], Training Accuracy: 93.7211%, Training Loss: 0.1999%
Epoch [299/300], Step [163/225], Training Accuracy: 93.7212%, Tra

Epoch [300/300], Step [27/225], Training Accuracy: 92.7662%, Training Loss: 0.2147%
Epoch [300/300], Step [28/225], Training Accuracy: 92.9129%, Training Loss: 0.2131%
Epoch [300/300], Step [29/225], Training Accuracy: 93.1573%, Training Loss: 0.2087%
Epoch [300/300], Step [30/225], Training Accuracy: 93.2292%, Training Loss: 0.2091%
Epoch [300/300], Step [31/225], Training Accuracy: 93.1956%, Training Loss: 0.2097%
Epoch [300/300], Step [32/225], Training Accuracy: 93.2129%, Training Loss: 0.2087%
Epoch [300/300], Step [33/225], Training Accuracy: 93.2765%, Training Loss: 0.2074%
Epoch [300/300], Step [34/225], Training Accuracy: 93.2445%, Training Loss: 0.2065%
Epoch [300/300], Step [35/225], Training Accuracy: 93.1250%, Training Loss: 0.2074%
Epoch [300/300], Step [36/225], Training Accuracy: 93.1424%, Training Loss: 0.2074%
Epoch [300/300], Step [37/225], Training Accuracy: 93.1588%, Training Loss: 0.2082%
Epoch [300/300], Step [38/225], Training Accuracy: 92.9688%, Training Loss: 

Epoch [300/300], Step [131/225], Training Accuracy: 93.6546%, Training Loss: 0.2013%
Epoch [300/300], Step [132/225], Training Accuracy: 93.6080%, Training Loss: 0.2033%
Epoch [300/300], Step [133/225], Training Accuracy: 93.5973%, Training Loss: 0.2032%
Epoch [300/300], Step [134/225], Training Accuracy: 93.5751%, Training Loss: 0.2034%
Epoch [300/300], Step [135/225], Training Accuracy: 93.5532%, Training Loss: 0.2043%
Epoch [300/300], Step [136/225], Training Accuracy: 93.5777%, Training Loss: 0.2043%
Epoch [300/300], Step [137/225], Training Accuracy: 93.5675%, Training Loss: 0.2042%
Epoch [300/300], Step [138/225], Training Accuracy: 93.5802%, Training Loss: 0.2038%
Epoch [300/300], Step [139/225], Training Accuracy: 93.5814%, Training Loss: 0.2036%
Epoch [300/300], Step [140/225], Training Accuracy: 93.5826%, Training Loss: 0.2033%
Epoch [300/300], Step [141/225], Training Accuracy: 93.5616%, Training Loss: 0.2035%
Epoch [300/300], Step [142/225], Training Accuracy: 93.5849%, Tra

In [17]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 58.532518065591994 %
